In [1]:
import webhoseio, os
from gensim.models import KeyedVectors
import json
from simhash import Simhash, SimhashIndex
import numpy as np

model_path = '/home/elia/Dropbox/Harrisburg/ANLY_610/codes/models/wordvec/'
data_path = '/home/elia/Dropbox/Harrisburg/ANLY_610/codes/data/'

In [2]:
def load_webhouse_data(data_name): 
    data_file = data_path + data_name + '.json'
    with open(data_file) as json_data:
        data = json.load(json_data)
        return data
    
data = load_webhouse_data('trump')

### Load Word Vector Model

In [3]:
def load_wordvec_model(modelName, modelFile, flagBin):
    print('Loading ' + modelName + ' model...')
    model = KeyedVectors.load_word2vec_format(model_path + modelFile, binary=flagBin)
    print('Finished loading ' + modelName + ' model...')
    return model

model_w2v_AP    = load_wordvec_model('Word2Vec Google News', 'GoogleNews-vectors-negative300.bin.gz', True)
#model_fasttext = load_wordvec_model('FastText', 'fastText_wiki_en.vec', False)

Loading Word2Vec Google News model...
Finished loading Word2Vec Google News model...


In [4]:
# function checks whether the input words are present in the vocabulary for the model
def vocab_check(vectors, words):
    output = list()
    for word in words:
        if word in vectors.vocab:
            output.append(word.strip())
            
    return output

In [5]:
# function calculates similarity between two strings using a particular word vector model
def calc_similarity(input1, input2, vectors):
    s1words = set(vocab_check(vectors, input1.split()))
    s2words = set(vocab_check(vectors, input2.split()))
    
    output = vectors.n_similarity(s1words, s2words)
    return output

In [6]:
def cleanup(input):
    # remove English stopwords
    input = input.replace("'s", " ").replace("n’t", " not").replace("’ve", " have")
    input = re.sub(r'[^a-zA-Z0-9 ]', '', input)
    return input

### Load data stored in json file

In [7]:
def load_webhouse_data(data_name): 
    data_file = data_path + data_name + '.json'
    with open(data_file) as json_data:
        data = json.load(json_data)
        return data
    
data = load_webhouse_data('trump')

### Print original dataset titles only

In [8]:
feeds = []
i = 0
for feed in data:
    feed['id'] = i
    i += 1
    feeds.append(feed)
print(feed['id'], str(feed['title']))

9999 Trump to ask Congress for 8.6 billion dollars for border wall in budget


### Define distance, index using SimHash, calculate duplicates subset using SimHash only

In [9]:
distance = 15
objs = [(str(feed['id']), Simhash(str(feed['title']))) for feed in feeds]
index_simahs = SimhashIndex(objs, k=distance)

In [10]:
# Select a feed from the list based on its index
SELECTED_INDEX = 10
feed_sel = feeds[SELECTED_INDEX]
print(feed_sel['title'])

Trump surveys devastation in Alabama, pays respects to tornado victims


In [12]:
# calculate  hash value
feed_hash = Simhash(str(feed_sel['title']))
# find all duplicate indices
dup_indices = index_simahs.get_near_dups(feed_hash)
print("Number of duplicates (SimHash): " + str(len(dup_indices)))

Big bucket found. key:c:0, len:664
Big bucket found. key:8:1, len:557
Big bucket found. key:2:2, len:1114
Big bucket found. key:f:3, len:486
Big bucket found. key:5:4, len:476
Big bucket found. key:b:5, len:781
Big bucket found. key:8:6, len:783
Big bucket found. key:4:7, len:520
Big bucket found. key:d:8, len:1344
Big bucket found. key:9:9, len:1291
Big bucket found. key:e:a, len:396
Big bucket found. key:1:b, len:688
Big bucket found. key:4:c, len:964
Big bucket found. key:1:d, len:904
Big bucket found. key:3:e, len:760
Big bucket found. key:c:f, len:443


Number of duplicates (SimHash): 37


### Print SimHash-based duplicate titles

In [13]:
for dupi in dup_indices:
    print(feeds[int(dupi)]['title'])

Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation in Alabama, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump Surveys Devastation, Pays Respects to Tornado Victims
Trump offers budget with funds for border wall, Space Force - KATC.com
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation in Alabama, pays respects to tornado victims
Trump Surveys Devastation, Pays Respects to Tornado Victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump s

### Calculate and print SimHash + Word2Vec similarity based duplicate titles

In [14]:
count_dup = 0
print("Original: " + feed_sel['title'])
print()
for dupi in dup_indices:
    try:
        score = calc_similarity(feed_sel['title'], feeds[int(dupi)]['title'], model_w2v_AP)
    except:
        score = 0
    if score > 0.55:
        count_dup += 1
        print(feeds[int(dupi)]['title'])
print("Number of Dupies (SimHash + WordVectors): " + str(count_dup))

Original: Trump surveys devastation in Alabama, pays respects to tornado victims

Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation in Alabama, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump Surveys Devastation, Pays Respects to Tornado Victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation in Alabama, pays respects to tornado victims
Trump Surveys Devastation, Pays Respects to Tornado Victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado victims
Trump surveys devastation, pays respects to tornado vict

# Clean list of titles from duplicates

In [61]:
def remove_duplicate(feed_sel, feeds, index_simahs, model_w2v_AP):
    duplicates = set()
    # calculate  hash value
    feed_hash = Simhash(str(feed_sel['title']))
    # find all duplicate indices
    dup_indices = index_simahs.get_near_dups(feed_hash)
    # apply word2vec 
    for dupi in dup_indices:
        try:
            score = calc_similarity(feed_sel['title'], feeds[int(dupi)]['title'], model_w2v_AP)
        except:
            score = 0
        if score > 0.55:
            duplicates.add(int(dupi))
    return duplicates

In [62]:
distance = 15
objs = [(str(feed['id']), Simhash(str(feed['title']))) for feed in feeds]
index_simahs = SimhashIndex(objs, k=distance)

duplicates = set()
for index in range(len(feeds)): 
    if index in duplicates: 
        continue 
    feed_sel = feeds[index]
    new_duplicates = remove_duplicate(feed_sel, new_feeds, index_simahs, model_w2v_AP)
    duplicates =duplicates.union(new_duplicates)
    if index % 50 == 0: 
        print(index, len(duplicates))

Big bucket found. key:c:0, len:664
Big bucket found. key:1:1, len:678
Big bucket found. key:e:2, len:620
Big bucket found. key:4:3, len:878
Big bucket found. key:0:4, len:807
Big bucket found. key:8:5, len:521
Big bucket found. key:b:6, len:794
Big bucket found. key:a:7, len:625
Big bucket found. key:0:8, len:663
Big bucket found. key:0:9, len:535
Big bucket found. key:7:a, len:802
Big bucket found. key:6:b, len:762
Big bucket found. key:3:c, len:263
Big bucket found. key:0:d, len:1273
Big bucket found. key:7:e, len:1111
Big bucket found. key:7:f, len:876
Big bucket found. key:e:0, len:1140
Big bucket found. key:0:1, len:875
Big bucket found. key:5:2, len:659
Big bucket found. key:e:3, len:822
Big bucket found. key:1:4, len:789
Big bucket found. key:f:5, len:793
Big bucket found. key:a:6, len:675
Big bucket found. key:6:7, len:450
Big bucket found. key:f:8, len:911
Big bucket found. key:8:9, len:744
Big bucket found. key:f:a, len:500
Big bucket found. key:b:b, len:430
Big bucket found.

0 1


Big bucket found. key:d:3, len:715
Big bucket found. key:1:4, len:789
Big bucket found. key:5:5, len:720
Big bucket found. key:0:6, len:581
Big bucket found. key:4:7, len:520
Big bucket found. key:3:8, len:582
Big bucket found. key:5:9, len:394
Big bucket found. key:9:a, len:679
Big bucket found. key:c:b, len:713
Big bucket found. key:d:c, len:899
Big bucket found. key:c:d, len:506
Big bucket found. key:2:e, len:531
Big bucket found. key:e:f, len:367
Big bucket found. key:c:0, len:664
Big bucket found. key:b:1, len:562
Big bucket found. key:2:2, len:1114
Big bucket found. key:7:3, len:539
Big bucket found. key:5:4, len:476
Big bucket found. key:9:5, len:715
Big bucket found. key:8:6, len:783
Big bucket found. key:4:7, len:520
Big bucket found. key:d:8, len:1344
Big bucket found. key:9:9, len:1291
Big bucket found. key:c:a, len:755
Big bucket found. key:1:b, len:688
Big bucket found. key:4:c, len:964
Big bucket found. key:1:d, len:904
Big bucket found. key:3:e, len:760
Big bucket found.

Big bucket found. key:2:d, len:636
Big bucket found. key:c:e, len:410
Big bucket found. key:0:f, len:951
Big bucket found. key:c:0, len:664
Big bucket found. key:5:1, len:723
Big bucket found. key:6:2, len:988
Big bucket found. key:b:3, len:375
Big bucket found. key:5:4, len:476
Big bucket found. key:b:5, len:781
Big bucket found. key:0:6, len:581
Big bucket found. key:5:7, len:467
Big bucket found. key:5:8, len:887
Big bucket found. key:9:9, len:1291
Big bucket found. key:b:a, len:275
Big bucket found. key:e:b, len:526
Big bucket found. key:5:c, len:915
Big bucket found. key:8:d, len:762
Big bucket found. key:7:e, len:1111
Big bucket found. key:5:f, len:1230
Big bucket found. key:8:0, len:403
Big bucket found. key:0:1, len:875
Big bucket found. key:a:2, len:637
Big bucket found. key:b:3, len:375
Big bucket found. key:c:4, len:703
Big bucket found. key:9:5, len:715
Big bucket found. key:3:6, len:670
Big bucket found. key:9:7, len:769
Big bucket found. key:b:8, len:531
Big bucket found.

Big bucket found. key:9:7, len:769
Big bucket found. key:f:8, len:911
Big bucket found. key:9:9, len:1291
Big bucket found. key:d:a, len:862
Big bucket found. key:7:b, len:829
Big bucket found. key:4:c, len:964
Big bucket found. key:c:d, len:506
Big bucket found. key:4:e, len:679
Big bucket found. key:e:f, len:367
Big bucket found. key:b:0, len:419
Big bucket found. key:4:1, len:691
Big bucket found. key:e:2, len:620
Big bucket found. key:e:3, len:822
Big bucket found. key:5:4, len:476
Big bucket found. key:6:5, len:418
Big bucket found. key:d:6, len:667
Big bucket found. key:f:7, len:496
Big bucket found. key:5:8, len:887
Big bucket found. key:e:9, len:543
Big bucket found. key:2:a, len:303
Big bucket found. key:8:b, len:383
Big bucket found. key:c:c, len:949
Big bucket found. key:8:d, len:762
Big bucket found. key:a:e, len:452
Big bucket found. key:b:f, len:374
Big bucket found. key:6:0, len:1128
Big bucket found. key:6:1, len:1040
Big bucket found. key:8:2, len:406
Big bucket found.

...

9950 1113


Big bucket found. key:b:8, len:531
Big bucket found. key:a:9, len:664
Big bucket found. key:d:a, len:862
Big bucket found. key:9:b, len:326
Big bucket found. key:c:c, len:949
Big bucket found. key:f:d, len:267
Big bucket found. key:7:e, len:1111
Big bucket found. key:e:f, len:367
Big bucket found. key:f:0, len:764
Big bucket found. key:0:1, len:875
Big bucket found. key:6:2, len:988
Big bucket found. key:8:3, len:836
Big bucket found. key:5:4, len:476
Big bucket found. key:5:5, len:720
Big bucket found. key:9:6, len:959
Big bucket found. key:1:7, len:678
Big bucket found. key:d:8, len:1344
Big bucket found. key:7:9, len:294
Big bucket found. key:d:a, len:862
Big bucket found. key:f:b, len:440
Big bucket found. key:0:c, len:727
Big bucket found. key:1:d, len:904
Big bucket found. key:3:e, len:760
Big bucket found. key:0:f, len:951
Big bucket found. key:e:0, len:1140
Big bucket found. key:7:1, len:661
Big bucket found. key:0:2, len:1004
Big bucket found. key:d:3, len:715
Big bucket found

Big bucket found. key:d:2, len:264
Big bucket found. key:6:3, len:546
Big bucket found. key:4:4, len:570
Big bucket found. key:9:5, len:715
Big bucket found. key:a:6, len:675
Big bucket found. key:2:7, len:789
Big bucket found. key:8:8, len:509
Big bucket found. key:2:9, len:525
Big bucket found. key:6:a, len:663
Big bucket found. key:6:b, len:762
Big bucket found. key:2:c, len:328
Big bucket found. key:6:d, len:648
Big bucket found. key:f:e, len:771
Big bucket found. key:d:f, len:465
Big bucket found. key:7:0, len:726
Big bucket found. key:f:1, len:408
Big bucket found. key:3:2, len:519
Big bucket found. key:9:3, len:538
Big bucket found. key:5:4, len:476
Big bucket found. key:2:5, len:702
Big bucket found. key:f:6, len:646
Big bucket found. key:5:7, len:467
Big bucket found. key:5:8, len:887
Big bucket found. key:0:9, len:535
Big bucket found. key:3:a, len:390
Big bucket found. key:2:b, len:587
Big bucket found. key:6:c, len:701
Big bucket found. key:6:d, len:648
Big bucket found. ke

Big bucket found. key:9:c, len:411
Big bucket found. key:b:d, len:379
Big bucket found. key:0:e, len:473
Big bucket found. key:b:f, len:374
Big bucket found. key:4:0, len:842
Big bucket found. key:9:1, len:552
Big bucket found. key:6:2, len:988
Big bucket found. key:e:3, len:822
Big bucket found. key:f:4, len:605
Big bucket found. key:5:5, len:720
Big bucket found. key:b:6, len:794
Big bucket found. key:9:7, len:769
Big bucket found. key:c:8, len:596
Big bucket found. key:b:9, len:1242
Big bucket found. key:0:a, len:572
Big bucket found. key:0:b, len:594
Big bucket found. key:4:c, len:964
Big bucket found. key:8:d, len:762
Big bucket found. key:3:e, len:760
Big bucket found. key:a:f, len:315
Big bucket found. key:1:0, len:355
Big bucket found. key:a:1, len:491
Big bucket found. key:5:2, len:659
Big bucket found. key:4:3, len:878
Big bucket found. key:4:4, len:570
Big bucket found. key:b:5, len:781
Big bucket found. key:a:6, len:675
Big bucket found. key:b:7, len:754
Big bucket found. k

Big bucket found. key:0:5, len:872
Big bucket found. key:b:6, len:794
Big bucket found. key:a:7, len:625
Big bucket found. key:d:8, len:1344
Big bucket found. key:b:9, len:1242
Big bucket found. key:5:a, len:1329
Big bucket found. key:c:b, len:713
Big bucket found. key:c:c, len:949
Big bucket found. key:9:d, len:797
Big bucket found. key:3:e, len:760
Big bucket found. key:9:f, len:385
Big bucket found. key:4:0, len:842
Big bucket found. key:7:1, len:661
Big bucket found. key:e:2, len:620
Big bucket found. key:f:3, len:486
Big bucket found. key:e:4, len:719
Big bucket found. key:0:5, len:872
Big bucket found. key:b:6, len:794
Big bucket found. key:a:7, len:625
Big bucket found. key:d:8, len:1344
Big bucket found. key:b:9, len:1242
Big bucket found. key:5:a, len:1329
Big bucket found. key:c:b, len:713
Big bucket found. key:c:c, len:949
Big bucket found. key:9:d, len:797
Big bucket found. key:3:e, len:760
Big bucket found. key:9:f, len:385
Big bucket found. key:1:0, len:355
Big bucket fou

In [63]:
new_feeds = feeds.copy()
for dup in sorted([int(dup) for dup in duplicates], reverse=True):
    del new_feeds[dup]

In [64]:
def store_data(data_name, feeds): 
    data_file = data_path + data_name + '.json'
    if os.path.isfile(data_file): 
        raise ValueError("{} file already exists".format(data_file))
    with open(data_file, 'w') as outfile:
        json.dump(feeds, outfile)
        
    
data = store_data('trump_clean', new_feeds)

In [65]:
data = load_webhouse_data('trump_clean')

In [70]:
data[10]['title']
objs = [(str(feed['id']), Simhash(str(feed['title']))) for feed in data]
index_simahs = SimhashIndex(objs, k=distance)
duplicate = remove_duplicate(data[10], data, index_simahs, model_w2v_AP)
print("Number of duplicates (SimHash + Word2Vec similarity): " + str(len(duplicate)))
for dup in duplicate: 
    print(data[dup]['title'])

Big bucket found. key:1d:0, len:371
Big bucket found. key:10:1, len:548
Big bucket found. key:11:2, len:536
Big bucket found. key:1f:3, len:300
Big bucket found. key:1d:6, len:249
Big bucket found. key:7:7, len:283
Big bucket found. key:15:8, len:540
Big bucket found. key:e:9, len:370


Number of duplicates (SimHash + Word2Vec similarity): 0
